# Árboles

## Curso "Introducción al Aprendizaje Automático"
## Facultad de Ingeniería
## UdelaR

El árbol de decisión es uno de los modelos más intuitivos del aprendizaje supervisado. Aprende a tomar decisiones dividiendo el espacio de datos en regiones cada vez más homogéneas, a partir de preguntas simples sobre los atributos.

In [ ]:
%pylab inline
import IPython
import sklearn as sk
import pandas as pd
import numpy as np
import matplotlib
import matplotlib.pyplot as plt


print('IPython version:', IPython.__version__)
print('numpy version:', np.__version__)
print('scikit-learn version:', sk.__version__)
print('pandas version:', pd.__version__)
print('matplotlib version:', matplotlib.__version__)

# Importar el dataset

Vamos a usar un dataset con personajes de los Simpsons, similar al que vimos en clase. Son datos sinteticos, de manera que puede contener errores.

La siguiente celda puede que no ejecute bien si corren localmente. Pueden descargar el archivo manualmente desde [este enlace](https://docs.google.com/spreadsheets/d/1nmBmgnPlkSyx8nsRKQAnBtkjIqIjEPTmxiX0dMvEADE/edit?usp=sharing)

In [ ]:
dataset_url ="https://drive.google.com/file/d/1mvvP2S0ltwFHOwluGn-zha2Ga3Kn3bPv/view?usp=sharing"

!pip install -q gdown

import gdown


# Use gdown to download
gdown.download(dataset_url, output=None, quiet=False, fuzzy=True)

La siguiente celda la ejecutamos para validar que el archivo este en el lugar adecuado:

In [ ]:
import os

# assert <condicion que deberia cumplirse>, "mensaje de error si la condicion anterior falla"
assert os.path.exists("toy_dataset.csv"), "El archivo no existe"

Leemos el csv, para esto vamos a usar `Pandas`: es una gran biblioteca para analisis de datos, no vamos a profundizar demasiado en ella en el curso.

In [ ]:
import pandas as pd

df = pd.read_csv("toy_dataset.csv")  # df es un DataFrame, muy similar a los de R

In [ ]:
df.columns

Index(['Nombre', 'Sexo', 'Edad', 'Grupo Etario', 'Pelo', 'Color de piel',
       'Color de pelo', 'Tiene barba', 'Tiene bigote', 'Usa collar',
       'Usa lentes', 'Usa caravanas', 'Usa corbata', 'Usa moño', 'Usa chupete',
       'Es fumador', 'Ocupación principal', 'Primer episodio', 'Apariciones',
       'Apariciones en especiales', 'Personaje principal'],
      dtype='object')

In [ ]:
n_instances, n_columns = df.shape
n_instances, n_columns

(88, 21)

In [ ]:
pd.set_option('display.max_columns', None)
df.head()

In [ ]:
df.columns

Index(['Nombre', 'Sexo', 'Edad', 'Grupo Etario', 'Pelo', 'Color de piel',
       'Color de pelo', 'Tiene barba', 'Tiene bigote', 'Usa collar',
       'Usa lentes', 'Usa caravanas', 'Usa corbata', 'Usa moño', 'Usa chupete',
       'Es fumador', 'Ocupación principal', 'Primer episodio', 'Apariciones',
       'Apariciones en especiales', 'Personaje principal'],
      dtype='object')

In [ ]:
# vemos el tipo de datos que hay en cada columna:
df.dtypes

In [ ]:
def str_to_bool(x):
  return x.strip().lower() != "no"

boolean_features = ['Tiene barba', 'Tiene bigote', 'Usa collar', 'Usa lentes', 'Usa caravanas', 'Usa corbata', 'Usa moño','Usa chupete', 'Es fumador']
target = "Personaje principal"

for c in boolean_features + [target]:
  df[c] = df[c].apply(str_to_bool)

df.dtypes


## Distribución de las clases en target

Vemos como se distribuye la columna "Personaje principal"

In [ ]:
import matplotlib.pyplot as plt
import numpy as np

# Contar la frecuencia de cada clase en y_train
class_name, class_counts = np.unique(df["Personaje principal"], return_counts=True)

for name, count in zip(class_name, class_counts):
    print(f"Clase: {name}, {count} ejemplos, {count/class_counts.sum()*100:.2f}%")

plt.title('Proporción de cada clase en el conjunto de entrenamiento')
plt.xlabel('Clase')
plt.ylabel('Proporción')
plt.bar(class_name, class_counts/class_counts.sum())
plt.xticks(class_name, [False, True], rotation=45, ha='right')
plt.tight_layout()
plt.show()

Partimos el dataset en train y test. El test no lo vamos a usar.

In [ ]:
from sklearn.model_selection import train_test_split

X = df.drop("Personaje principal", axis=1)
y = df["Personaje principal"]

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y, shuffle=True)

print("Shape of X_train:", X_train.shape)
print("Shape of X_test:", X_test.shape)
print("Shape of y_train:", y_train.shape)
print("Shape of y_test:", y_test.shape)

### Ejercicio

La siguiente celda muestra la [documentación de la función train_test_split](https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.train_test_split.html).

Contestar **qué estamos haciendo** con los siguientes parámetros y **por qué** son importantes:

- `random_state=42`:

- `stratify=y`:

- `shuffle=True`:



In [ ]:
train_test_split?

# Entrenar nuestro primer árbol

Comencemos por entrenar nuestro primer árbol, para el que vamos a usar unicamente las columnas booleanas

In [ ]:
from sklearn.tree import DecisionTreeClassifier

# Train a Decision Tree Classifier with default parameters
model = DecisionTreeClassifier(criterion="entropy", random_state=0)
model.fit(X_train[boolean_features], y_train)

In [ ]:

DecisionTreeClassifier?

In [ ]:
from sklearn.tree import plot_tree
import matplotlib.pyplot as plt

plt.figure(figsize=(12, 8), dpi=300) # Increase figsize and dpi
plot_tree(model, feature_names=boolean_features, class_names=['False', 'True'], filled=True, rounded=True)
plt.show()

Que performance obtuvimos? Para contestar esta pregunta, vamos a utilizar validación cruzada con 7 folds, midiendo para cada una de ellas la f-score

In [ ]:
from sklearn.model_selection import cross_val_score

# Perform cross-validation with 7 folds
cv_scores = cross_val_score(model, X_train[boolean_features], y_train, cv=7, scoring="f1")

print("cv_scores.shape = ", cv_scores.shape)
print("F-scores for each fold:", cv_scores)
print("Mean F-score:", cv_scores.mean())
print("Standard deviation of F-scores:", cv_scores.std())


Veamos que sucede si repetimos lo mismo, pero esta vez, limitamos la capacidad del arbol:

In [ ]:

DecisionTreeClassifier?

In [ ]:
shallow_tree = DecisionTreeClassifier(criterion="entropy", max_depth=4,
                                      min_samples_split=5, random_state=0)

shallow_tree.fit(X_train[boolean_features], y_train)

In [ ]:
from sklearn.tree import plot_tree
import matplotlib.pyplot as plt

plt.figure(figsize=(12, 8), dpi=300) # Increase figsize and dpi
plot_tree(shallow_tree, feature_names=boolean_features, class_names=['False', 'True'], filled=True, rounded=True)
plt.show()

Vemos la performance a la que llegamos:

In [ ]:

from sklearn.model_selection import cross_val_score

# Perform cross-validation with 7 folds
cv_scores = cross_val_score(shallow_tree, X_train[boolean_features], y_train, cv=7, scoring="f1")

print("cv_scores.shape = ", cv_scores.shape)
print("F-scores for each fold:", cv_scores)
print("Mean F-score:", cv_scores.mean())
print("Standard deviation of F-scores:", cv_scores.std())

# Busqueda de hiperparametros

Como sabemos que parametros deberiamos usar?

Este problema es la busqueda de hiperparametros: necesitamos saber como buscar los parametros que retornan mejores resultados. Vamos a explorar algunas formas de hacerlo, viendo pros y contras en cada caso.


Lo mas sencillo que podemos hacer es probar manualmente: consulten la documentacion de `DecisionTreeClassifier` para entender qué opciones tenemos y prueben modificar esos valores a ver como cambia la performance:

In [ ]:
DecisionTreeClassifier?

_Este ejercicio puede ser infinito: asegurense de probar al menos 3 configuraciones y no dediquen más de 10 min._

In [ ]:
manual_tree = DecisionTreeClassifier(criterion="entropy", max_depth=4,
                                      min_samples_split=5, random_state=0)

cv_scores = cross_val_score(manual_tree, X_train[boolean_features], y_train, cv=7, scoring="f1")


print(f"F-score {cv_scores.mean():.03f} ± {cv_scores.std():.03f}")

## Manual search
Es lo que hicimos antes, probar cosas que nos parecen razonables a partir de nuestro conocimiento (del problema y del algoritmo que estoy usando).


### Ejercicio:

A partir de lo que probaron antes, completar brevemente lo siguiente:

**Ventajas de este enfoque:** _completar_


**Desventajas: lento, toma**: _completar_

In [ ]:

DecisionTreeClassifier?

## Grid Search

Podria intentar automatizar esto, definiendo valores que quiero probar, por ejempo:

```python
max_depth_values = [2, 4, 8]
min_samples_split_values = [2, 5, 10, 20]

for max_depth in max_depth_values:
    for min_samples_split in min_samples_split_values:
        dt = DecisionTreeClassifier(criterion="entropy",
                                    max_depth=4,
                                    min_samples_split=5)
        # evaluo dt con validacion cruzada, me guardo el resultado
        
# retorno la configuracion que dio mejor resultado
```
Se llama `grid` porque de alguna manera estoy definiendo una grilla de parametros a probar: todas las combinaciones posibles entre los que elegi.

Por fortuna, scikit learn trae ya esto implementado, de manera que es muy sencillo de usar. El ejemplo del pseudo codigo anterior, utilizando [`GridSearchCV`](https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.GridSearchCV.html) es el siguiente:



In [ ]:
from sklearn.model_selection import GridSearchCV

# Define the parameter grid to search
param_grid = {
    'max_depth': [2,4, 8], # Maximum depth of the tree
    'min_samples_split': [2, 5, 10, 20] ,  # Function to measure the quality of a split

}
# param_grid es un diccionario que tiene como clave el nombre del parametro y como valor una lista con los valores a probar

n_configs = 7  # Usamos cv=7
for k,v in param_grid.items():
    n_configs *= len(v)
print("Number of trees to fit:", n_configs)
# parametros base a usar: si no sobreescribo en la rilla que defini, va a usar estos
tree = DecisionTreeClassifier(criterion="entropy", random_state=0)

# Create a GridSearchCV object
grid_search = GridSearchCV(estimator=tree,
                           param_grid=param_grid,
                           cv=7,  # Use 7-fold cross-validation
                           scoring='f1', # Score using f1
                           n_jobs=-1) # Use all available cores

# Fit the grid search to the data
grid_search.fit(X_train[boolean_features], y_train)

# Print the best parameters and the best score
print("Best parameters found:", grid_search.best_params_)
print("Best cross-validation F1 score:: {:.4f} ± {:.4f}".format(grid_search.best_score_, grid_search.cv_results_['std_test_score'][grid_search.best_index_]))

### Ejercicio:

1. Volver a la celda anterior y re-ejecutarla probando más combinaciones. Jueguen con otros parametros. Buscar una configuracion que reporte mejores numeros que la grid actual (0.4705).

2. A partir de lo que probaron antes, completar brevemente lo siguiente:

    - **Ventajas de este enfoque:** _completar_
    - **Desventajas de este enfoque**: _completar_

## Random Search

## 🔍 Random Search

Cuando probaron hiperparámetros a mano, lo hicieron más o menos al azar —y aun así lograron mejoras.

Random Search automatiza esa idea: en lugar de evaluar *todas* las combinaciones como en Grid Search, prueba un número limitado de configuraciones aleatorias.

In [ ]:
from sklearn.model_selection import RandomizedSearchCV
from scipy.stats import randint

# Define the parameter distributions to sample from
param_distributions = {
    'max_depth': [2,3,4,5,6,7,8,9,10,11,12,13,14,15],  # Integer values from 2 to 15
    'min_samples_split': randint(low=2, high=30), # Integer values from 2 to 29
}

# Define the number of iterations for the random search
n_iter_search = 12  # Number of parameter settings that are sampled.

print("Number of trees to fit:", n_iter_search * 7)

# Define the base model
tree = DecisionTreeClassifier(criterion="entropy", random_state=0)

# Create a RandomizedSearchCV object
random_search = RandomizedSearchCV(estimator=tree,
                                   param_distributions=param_distributions,
                                   n_iter=n_iter_search,
                                   cv=7,  # Use 7-fold cross-validation
                                   scoring='f1', # Score using f1
                                   random_state=42, # For reproducibility
                                   n_jobs=-1) # Use all available cores

# Fit the random search to the data
random_search.fit(X_train[boolean_features], y_train)

# Print the best parameters and the best score
print("Best parameters found:", random_search.best_params_)
print("Best cross-validation F1 score: {:.4f} ± {:.4f}".format(random_search.best_score_, random_search.cv_results_['std_test_score'][random_search.best_index_]))

### Ejercicio
1. Vuelvan a la celda anterior, agreguen mas parametros a probar y la cantidad de configuraciones a probar, similar a como lo hicimos en grid search.

2. A partir de lo que probaron antes, completar brevemente lo siguiente:

    - Ventajas de este enfoque: completar
    - Desventajas de este enfoque: completar

## Más allá del azar: optimización de hiperparámetros

Hasta ahora vimos tres estrategias: probar a mano, hacer una búsqueda exhaustiva (Grid Search) o al azar (Random Search).

Pero existe una alternativa más sofisticada: **plantear la búsqueda de hiperparámetros como un problema de optimización**.  
En lugar de probar combinaciones “porque sí”, estos métodos intentan **usar la información obtenida en pruebas anteriores para decidir qué probar después**.

Existen frameworks como **Optuna**, **Hyperopt** o **BayesSearchCV**, que implementan estrategias como búsqueda bayesiana o métodos de Monte Carlo para encontrar buenas configuraciones de manera más eficiente.

Estan fuera del alcance de curso, pero vale la pena saber que existen —y que en muchos casos reales, son una mejor opción.


# Y las otras features?

Hasta aca trabajamos solo con las features booleanas. Llegamos a resultados magros, probablemente porque las features no son muy utiles para distinguir a los personajes principales de los secundarios.

Entrenemos a continuacion un arbol con todas las features a ver que resultado tenemos:

In [ ]:
from sklearn.tree import DecisionTreeClassifier

# Train a Decision Tree Classifier with default parameters
model = DecisionTreeClassifier(criterion="entropy", random_state=0)
model.fit(X_train, y_train)

Por que fallo? El problema es que la implementaciond e scikit espera que todas las features sean numericas, pero tenemos muchos atributos categoricos, como el color de pelo o el nombre.

Como podemos pasar el color de pelo a nombre?

Esta etapa en general se le llama pre-procesamiento o codificacion de atributos.

Veamos que alternativas tenemos

# Preprocesamiento

Para fijar ideas, pensemos en el atributo "color de pelo": el objetivo es obtener un mapeo que me lleve el valor del atributo, a una representacion numerica.

Decimos que este mapeo lo _aprendemos_ porque lo vamos a inferir de los datos. Como todo lo que aprendemos, debemos hacerlo **unicamente con el dataset de entrenamiento**.

## One Hot Encoding

La idea es simple:  
por cada valor posible del atributo, agregamos una columna.  
En cada fila, todas las columnas tendrán 0, excepto la que corresponde al valor real, que tendrá un 1.

Por ejemplo, si la variable `color de pelo` puede valer `amarillo`, `azul` o `negro`, creamos tres columnas:


|color de pelo| color_amarillo | color_azul  | color_negro |
|-------------|----------------|-------------|-------------|
|'amarillo'   | 1              | 0           | 0           |
|'azul'       | 0              | 1           | 0           |
|'negro'      | 0              | 0           | 1           |


In [ ]:
import pandas as pd
from sklearn.preprocessing import OneHotEncoder
from IPython.display import display

# Select the categorical feature to encode
hair_color = X_train[['Color de pelo']]

print("Unique values for hair color:", np.unique(hair_color))

# Initialize the OneHotEncoder
# handle_unknown='ignore' allows the encoder to handle unseen categories in the test set
# sparse_output=False returns a dense numpy array instead of a sparse matrix
ohe = OneHotEncoder(handle_unknown='ignore',sparse_output=False)

ohe.fit(hair_color)

# Fit the encoder on the training data and transform it
hair_color_encoded = ohe.transform(hair_color)

# Get the new column names after encoding
new_feature_names = ohe.get_feature_names_out(['Color de pelo'])

# Create a new DataFrame with the one-hot encoded columns
hair_color_df = pd.DataFrame(hair_color_encoded, columns=new_feature_names, index=X_train.index)

# Display the first few rows of the new DataFrame
display(hair_color_df.head())

# Display the shape of the new DataFrame
print("\nShape of one-hot encoded hair color:", hair_color_df.shape)

# Display the categories learned by the encoder
print("\nCategories learned by the encoder:", ohe.categories_)

El objeto `ohe` aprendio el mapeo correspondiente que nos lleva de esos colores a su representacion numerica. Podemos usarlo ahora para codificar el valor "Azul" por ejemplo:

In [ ]:
ohe.transform([["Azul"]])

### Ejercicio
- Generar la representación para los colores "Amarillo" y "Violeta". Como son sus representaciones con respecto a la del "Azul"? Explicar qué sucede y qué implica.
- Explicar ventajas y desventajas que noten en este mecanismo.
    - _Pista: qué pasa si tengo muchos colores?_

## Ordinal Encoder
El principal problema que tiene OneHotEncoding es que agrega muchas columnas. Si bien puedo hacer alguna cosa para limitarlo (ejemplo: solo decido codificar los N mas frecuentes), ese tipo de cosas en general acarrean expresividad

Una forma sencilla de levantar esa restriccion es asignar a cada color un numero:

"amarillo" -> 0
"azul" -> 1
"negro" -> 2
"verde" -> 3
"blanco" -> 4

Con esto puedo representar todos los colores con un unico numero. El problema que tiene esto es que estoy forzando una relacion que no existe: por qué el azul está más cerca del amarillo que del blanco?

Sin embargo, puede ser muy util cuando efectivamente tengo una relacion de orden en mis datos: por ejemplo, veamos que pasa con el Grupo Etario:

In [ ]:
# Select the 'grupo etario' column
age_group = X_train[['Grupo Etario']]

# Check unique values and their order
print("Unique values for age group:", np.unique(age_group))

En estos casos existe cierto orten intrinseco: podemos ordenarlos perfectamente como `['Joven','Adulto', 'Adulto mayor']`, y de esta forma codificarlo con un solo numero, que además captura cierta relacion que se da en la realidad:

In [ ]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import OrdinalEncoder


# Define the desired order for the ordinal encoding
age_group_order = ['Joven','Adulto', 'Adulto mayor']

# Initialize the OrdinalEncoder with the specified order
oe = OrdinalEncoder(categories=[age_group_order], handle_unknown="use_encoded_value",unknown_value=-1)

# Fit the encoder on the training data and transform it
age_group_encoded = oe.fit_transform(age_group)

# Create a new DataFrame with the ordinal encoded column
age_group_df = pd.DataFrame(age_group_encoded, columns=['grupo etario_encoded'], index=X_train.index)

# Display the first few rows of the new DataFrame
display(age_group_df.head())

# Display the shape of the new DataFrame
print("\nShape of ordinal encoded age group:", age_group_df.shape)

# Display the categories learned by the encoder
print("\nCategories learned by the encoder:", oe.categories_)

# Example of transforming unseen data (e.g., a single value)
# Note: OrdinalEncoder handles unseen values differently depending on the handle_unknown parameter (default is 'error').
# If you might encounter unseen values in the test set, consider setting handle_unknown='use_encoded_value'
# and providing unknown_value (e.g., -1 or a value outside the defined range).
# For this example, let's transform a known value:
print("\nEncoding 'Adulto':", oe.transform([['Adulto']]))

En este caso, el objeto `oe` es elq ue guarda ese mapeo. Probemos transformar las categorias conocidas a ver si representacion:

In [ ]:
oe.transform([["Joven"], ["Adulto"],["Adulto mayor"]])

### Ejercicio
- Generar la representación para el grupo "Bebé" y para el grupo "Anciano". Como son sus representaciones con respecto a la de "Joven"? Explicar qué sucede y qué implica.

# Ingeniería de atributos: ¿Qué hacemos con el nombre?

Tenemos una columna `Nombre`, que hasta ahora no usamos.

En la clase anterior vimos que **se apellida “Simpson”** es una pista muy fuerte para saber si un personaje es principal. Entonces, podría ser útil usar el nombre... pero, ¿cómo?

In [ ]:
X["Nombre"]

## Ejercicio
Vimos como funciona `OneHotEncoder` y `OrdinalEncoder`: ¿cuál usarías para codificar el atributo `nombre`? Justifique brevemente.

Bien, el nombre en si tiene una cardinalidad muy alta, de hecho son todos nombres unicos: es un identificador. Codificarlo no me va a servir de mucho asi como viene. Ahora, este identificador, esconde cierta informacion, que, por nuestro conocimiento del dominio, sabemos que es util: el apellido Simpson.

La **ingeniería de atributos** consiste en transformar o crear nuevas variables a partir de las originales, para representar mejor la información relevante para el modelo.

En este caso:

- La variable nombre no es útil directamente.

- Sabemos algo del dominio: el apellido “Simpson” es relevante.

- Entonces, extraer el apellido es una forma de hacer ingeniería de atributos.

Esto también muestra que:

No todo lo que está en los datos sirve tal como viene.

Nuestro conocimiento del problema importa: no todo lo puede hacer automáticamente el modelo.



In [ ]:
def se_apellida_simpson(nombre):
  return "simpson" in nombre.lower()

# aca vamos a aplicar una funcion directo sobre los datos, en vez de  hacerlo con scikit
# la funcion `apply` al llamarla sobre una columna, toma cada fila de la columna
# y le aplica la funcion que pasamos por parametro, en este caso `se_apellida_simpson`
# El resultado lo guardamos en una nueva columna
X_train["apellido_simpson"] = X_train["Nombre"].apply(se_apellida_simpson)
# Importante: recuerden aplicar las modificaciones al test!
X_test["apellido_simpson"] = X_test["Nombre"].apply(se_apellida_simpson)

Otro punto en el que podemos hacer esta ingenieria de atributos, es combinandolos. Pensemos por ejemplo en las feaatures numericas que tiene el dataset:

In [ ]:
X_train[['Primer episodio', 'Apariciones','Apariciones en especiales']]

Algo que puedo hacer es combinar esta informacion para tener cosas mas claras. Por ejemplo, si divido la cantidad de apariciones en especiales que tuvo sobre el total de apariciones, voy a tener una idea de cuantos especiales participo respecto a la cantidad de episodios totales en los que participo.

Eso puedo hacerlo de esta forma:

In [ ]:
def ratio_especiales(row):
    """
    row: diccionario que representa la fila del dataframe,
    donde la clave es el nombre de la columna y el valor es el valor de esa
    columna para esa fila.

    El valor que vamos a retornar va a quedar asignado a la columna
    "ratio_especiales" que estamos creando
    """
    if row["Apariciones"] == 0:
        return 0
    return row["Apariciones en especiales"] / row["Apariciones"]

X_train["ratio_especiales"] = X_train.apply(ratio_especiales, axis=1)
X_test["ratio_especiales"] = X_test.apply(ratio_especiales, axis=1)

### Ejercicio
Implementar las funciones `new_feature_uno` y `new_feature_dos` para generar dos features nuevas a partir de todas las que tienen hasta el momento. Deben ser features numericas (retornar `float`, `int` o `bool`).

_Importante: no renombren las funciones!_


In [ ]:
def new_feature_uno(row):
    """
    row: diccionario que representa la fila del dataframe,
    donde la clave es el nombre de la columna y el valor es el valor de esa
    columna para esa fila.

    El valor que vamos a retornar va a quedar asignado a la columna
    "ratio_especiales" que estamos creando
    """
    # completen aca
    return 1

X_train["new_feature_uno"] = X_train.apply(new_feature_uno, axis=1)
X_test["new_feature_uno"] = X_test.apply(new_feature_uno, axis=1)

In [ ]:
def new_feature_dos(row):
    """
    row: diccionario que representa la fila del dataframe,
    donde la clave es el nombre de la columna y el valor es el valor de esa
    columna para esa fila.

    El valor que vamos a retornar va a quedar asignado a la columna
    "ratio_especiales" que estamos creando
    """
    # completen aca
    return 2

X_train["new_feature_dos"] = X_train.apply(new_feature_dos, axis=1)
X_test["new_feature_dos"] = X_test.apply(new_feature_dos, axis=1)

ahora es momento de usar todas estas features para generar un arbol:

In [ ]:
import pandas as pd
# Identificar columnas categóricas y numéricas
categorical_features = ['Sexo', 'Grupo Etario', 'Pelo', 'Color de piel',
                          'Color de pelo']
numerical_features = ['Edad', 'Tiene barba', 'Tiene bigote', 'Usa collar',
                        'Usa lentes', 'Usa caravanas', 'Usa corbata', 'Usa moño',
                        'Usa chupete','Es fumador', 'Primer episodio', 'Apariciones',
                        'Apariciones en especiales', 'apellido_simpson',
                        'new_feature_uno', 'new_feature_dos']


# Aplicar One-Hot Encoding a las características categóricas
# Creamos una instancia del OneHotEncoder
ohe_encoder = OneHotEncoder(handle_unknown='ignore', sparse_output=False)

# Entrenamos el encoder con los datos de entrenamiento
ohe_encoder.fit(X_train[categorical_features])

# Transformamos los datos de entrenamiento y prueba
X_train_categorical_encoded = ohe_encoder.transform(X_train[categorical_features])
X_test_categorical_encoded = ohe_encoder.transform(X_test[categorical_features])

# Obtenemos los nombres de las nuevas columnas creadas por el OneHotEncoder
new_categorical_feature_names = ohe_encoder.get_feature_names_out(categorical_features)

# Creamos DataFrames con las características categóricas codificadas
X_train_categorical_df = pd.DataFrame(X_train_categorical_encoded,
                                      columns=new_categorical_feature_names,
                                      index=X_train.index)
X_test_categorical_df = pd.DataFrame(X_test_categorical_encoded,
                                     columns=new_categorical_feature_names,
                                     index=X_test.index)

# Concatenamos las características numéricas originales con las categóricas codificadas
X_train_processed = pd.concat([X_train[numerical_features], X_train_categorical_df], axis=1)
X_test_processed = pd.concat([X_test[numerical_features], X_test_categorical_df], axis=1)


# Definir el modelo de Árbol de Decisión con parámetros por defecto
# Usamos criterion='entropy' como en los ejemplos anteriores, pero los demás son los por defecto
model_full_features = DecisionTreeClassifier(criterion="entropy", random_state=0)

# Entrenar el modelo con todas las características preprocesadas
model_full_features.fit(X_train_processed, y_train)

# Evaluar el modelo usando validación cruzada
cv_scores_full_features = cross_val_score(model_full_features, X_train_processed, y_train, cv=7, scoring="f1")

print("cv_scores_full_features.shape = ", cv_scores_full_features.shape)
print("F-scores for each fold (full features):", cv_scores_full_features)
print("Mean F-score (full features):", cv_scores_full_features.mean())
print("Standard deviation of F-scores (full features):", cv_scores_full_features.std())

### Ejercicio:
Encontrar los mejores parametros para entrenar un arbol con `X_train_processed, y_train` siguiendo alguno de los metodos vistos antes. Reportar la mejor medida f-1 en cada caso, utilizando validacion cruzada

In [ ]:

# entrenarlo, buscar mejores parametros, reportar metrica obtenida

# ¿El árbol o el bosque?

Hasta ahora entrenamos un solo árbol de decisión. Pero, ¿y si usamos varios?



## Random Forest: muchos árboles que trabajan en paralelo
- Entrena muchos árboles distintos y los hace votar.
- Cada árbol ve una parte diferente de los datos y elige entre distintas preguntas.
- Como no todos cometen los mismos errores, la combinación suele ser más precisa y confiable que un solo árbol.






## HistGradientBoostingClassifier: árboles que aprenden de los errores
- Entrena los árboles uno después del otro.
- Cada nuevo árbol intenta corregir lo que los anteriores hicieron mal.
- Es una forma muy efectiva de mejorar progresivamente el modelo.


### Ejercicio (Opcional)

Entrenar un `RandomForestClassifier` y un `HistGradientBoostingClassifier` usando los datos `X_train_processed`.


In [ ]:
from sklearn.ensemble import RandomForestClassifier, HistGradientBoostingClassifier

# entrenarlo, buscar mejores parametros, reportar metrica obtenida

# Hora del Test-set!
Hora de la evaluacion final!

- Instanciar el mejor modelo logrado hasta el momento, con los mejores parametros
- Entrenarlo con todos los datos de entrenamiento
- Predecir sobre el conjunto de test

In [ ]:

best_model = RandomForestClassifier()

best_model.fit(X_train_processed, y_train)
y_pred = best_model.predict(X_test_processed)

In [ ]:
from sklearn.metrics import classification_report
print(classification_report(y_test, y_pred))

Por ultimo vemos la matriz de confusion:

In [ ]:
import matplotlib.pyplot as plt
from sklearn.metrics import confusion_matrix
import seaborn as sns

# Generate the confusion matrix
cm = confusion_matrix(y_test, y_pred)

# Plot the confusion matrix
plt.figure(figsize=(8, 6))
sns.heatmap(cm, annot=True, fmt='d', cmap='Blues')
plt.xlabel('Predicted')
plt.ylabel('Actual')
plt.title('Confusion Matrix')
plt.show()